# DSP homework 2: Make music using Karplus-String algorithm
(Designed by: Massoud Babaie-Zadeh)

Karplus-Strong algorithm is a method for artificially synthesizing the sound of a hammered or plucked string. It is based on the following system:

![image](Karplus-strong-schematic.png)

In the EPFL (coursera) slides that we saw in the class, the filter in the return path is the identity filter with a gain $\alpha$ (moreover, instead of $L$, the letter $M$ is used). So, in EPFL slides, the difference equation of the whole system is:

$$
y[n] = x[n] + \alpha y[n-M]
$$

The input of the system ($x[n]$) is a random sequence of length $M$ (the same value as delay in the feedback path).

But it is better to have a moving average (MA) filter of length 2 in the return path. So, a more correct version is:

$$
y[n] = x[n] + \alpha \,  \frac{y[n-M] + y[n-M-1]}{2}
$$

A common choice for $\alpha$ is 0.994. The value of $M$ is defined by the pitch of the tone that we are synthesizing (note that the output of the above systems is quasi-periodic with period of $M$ samples).

In this homework:
- You implement both of the above systems and compare their outputs.
- You will have a better understanding of how discrete signals are played as analog signals, and how samples and physical times are related to each other.
- You will learn how to play audio in Python.

In [2]:
import numpy as np

fs = 44100  # Sampling frequency used throught this notebook

In [60]:
# Implementing the algorithm as stated in EPFL slides
def make_note_EPFL_slides(freq, duration, fs=44100, alpha=0.99):   # freq in Hz, duration in mili-seconds. No filter in feedback path
    
    # YOUR CODE STARTS HERE (note that 'sig_len' and 'M' should be integers)
    sig_len = int(fs*duration / 1000)
    M = int(fs / freq)   # period in samples
    # YOUR CODE ENDS HERE
    
    # Create a random sequence of length M, and mean 0
    x = np.random.rand(M) - 0.5
    
    # Create a buffer (place holder) for the whole output signal y
    y = np.zeros(sig_len)
    
    # Implementing the difference equation y[n]=x[n]+alpha*y[n-M].
    # Note that by definition x[n]=0 for n>=M and for n<0.
    # YOUR CODE STARTS HERE
    for i in range(M) :
        y[i] = x[i]
    for i in range(sig_len - M) :
        y[i + M] = alpha*y[i]
     # YOUR CODE ENDS HERE
    
    return y

In [61]:
x = make_note_EPFL_slides(440, 2000)

Now we  have generated a signal (x), which is a numpy array, and we would like to play it as an audio signal. To know about different methods of playing/recording/converting audio signals in Python, refer to [here](https://realpython.com/playing-and-recording-sound-python/).

Besides the methods stated in the above link, if you are using jupyter notebooks, you can use the following simple method to play a signal as audio:

In [62]:
from IPython.display import Audio

Audio(x,rate=fs)

Now, we implement the second system (with MA filter of length 2 in the feedback path):

In [52]:
# Implementing the more correct algorithm
def make_note(freq, duration, alpha=0.994, fs=44100):   # freq in Hz, duration in mili-seconds. Average filter in feedback path
    
    # YOUR CODE STARTS HERE (note that 'sig_len' and 'M' should be integers)
    sig_len = int(fs*duration / 1000)
    M = int(fs / freq)   # period in samples
    # YOUR CODE ENDS HERE
    
    # Create a random sequence of length M, and mean 0
    x = np.random.rand(M) - 0.5
    
    # Create a buffer (place holder) for the whole output signal y
    y = np.zeros(sig_len)
    
    # Implementing the difference equation y[n]=x[n]+alpha*(y[n-M]+y[n-M-1])/2.
    # Note that by definition x[n]=0 for n>=M and for n<0.
    # YOUR CODE STARTS HERE
    for i in range(M) :
        y[i] = x[i]
    y[M] = alpha*y[0] / 2
    
    for i in range(sig_len - M - 1) :
        y[i + M + 1] = alpha*(y[i + 1] + y[i]) / 2
    
    # YOUR CODE ENDS HERE
    
    return y

In [53]:
x = make_note(440, 2000, alpha=0.994)
Audio(x,rate=fs)

Please listen to both of the above generated tones. Moreover, besides the default value of $\alpha=0.994$, try also $\alpha=0.999$ and $\alpha=0.98$: generate the signals, play and compare them:

In [54]:
x = make_note(440, 2000, alpha=0.999)
Audio(x,rate=fs)

In [55]:
x = make_note(440, 2000, alpha=0.98)
Audio(x,rate=fs)

$\alpha$ is decay factor and controls envelop of the signal. For $\alpha=0.98$ the signal is attenuated faster than $\alpha=0.994$ and for $\alpha=0.994$ the signal is attenuated faster than $\alpha=0.999$

Now, we would like to write a function that creates a sequence of notes. We call it 'make_song':

In [56]:
def make_song(notes, durations=None):
    """
    The functions receives two lists or two numpy arrays (the lengths should be the same): 'notes' and
    'durations'.
    
    'notes' is a sequence of strings (eg. 'A4', 'B2', etc, representing diffrent music notes). 
    
    All of the valid notes and their corresponding frequencies are in the dictionary
    'music_dictionary_of_freqs', returned by the function 'make_music_dictionary_of_freqs'. Note that the name of the notes
    are different in different countries (eg in France 'do re mi fa ...', and in Engilsh 'C D E F ...'). So,
    if use this program for different standards of different countries, the only function that has to be changed
    is 'make_music_dictionary_of_freqs', which makes the 'music_dictionary_of_freqs' for that standard.
    
    'durations' is the duration (in mili-seconds) of playing each note.
    
    duration can be omitted. It this case, all notes are played for the fixed amount of 550ms.
    
    duration can also be a single integer. In this case, all notes are played for this fixed amount.
    """
        
    if durations is None:   # If 'durations' is not provided, the default is to use equal durations (550ms) for all notes
        durations = 550 * np.ones(len(notes))
    elif isinstance(durations, int):  # If only one integer is provided => Play all notes with this duration
        durations = durations * np.ones(len(notes))
        
    music_dictionary_of_freqs = make_music_dictionary_of_freqs()
    
    if len(notes) != len(durations):
        print('error in "make_song()": lengths of input arrays should be equal')
    
    
    x = np.array([]) # Start with an empty array. Then create each notes one-by-one and append (concatenate)
                     # them to this signal, using 'np.concatenate' function.
    xc = np.array([])
    for i in range(len(notes)):
        note = notes[i]
        duration = durations[i]
        # YOUR CODE STARTS HERE
        freq = music_dictionary_of_freqs[note]
        xc = make_note(freq, duration)
        x = np.concatenate((x, xc))
        # YOUR CODE ENDS HERE
        
    return(x)

In [57]:
def make_music_dictionary_of_freqs():

    # Reference about notes and their frequencies: https://en.wikipedia.org/wiki/Musical_note

    notes = ['C','C#','D','D#','E','F','F#','G','G#','A','A#','B','high_C']
    
    A = 440                # A4
    C5 = A * 2 ** (3/12)
    C = C5 / 2             # C4
    
    music_dictionary_of_freqs = {}
    for (i, note) in enumerate(notes):
        freq = C * 2 ** (i/12)
        music_dictionary_of_freqs[note] = freq
        
    return(music_dictionary_of_freqs)

Play all notes in our dictionary:

In [58]:
notes = ['C','C#','D','D#','E','F','F#','G','G#','A','A#','B','high_C']
x=make_song(notes)
Audio(x,rate=fs)

Now play the following song ([Reference](https://noobnotes.net/twinkle-twinkle-little-star-traditional/)):

In [59]:
notes=['C', 'C', 'G', 'G', 'A', 'A', 'G', 
       'F', 'F', 'E', 'E', 'D', 'D', 'C',
       'G', 'G', 'F', 'F', 'E', 'E', 'D',
       'G', 'G', 'F', 'F', 'E', 'E', 'D',
       'C', 'C', 'G', 'G', 'A', 'A', 'G', 
       'F', 'F', 'E', 'E', 'D', 'D', 'C', ]
durations=[550, 550, 550, 550, 550, 550, 1100, 
           550, 550, 550, 550, 550, 550, 1100,
           550, 550, 550, 550, 550, 550, 1100, 
           550, 550, 550, 550, 550, 550, 1100,
           550, 550, 550, 550, 550, 550, 1100, 
           550, 550, 550, 550, 550, 550, 1100]
x=make_song(notes, durations)
Audio(x,rate=fs)

You can also play with the above codes. For example, in 'make_music_dictionary_of_freqs()', instead of 'C = C5 / 2', you can use 'C = C5' to play the above song in a higher octave.